In [ ]:
import pandas as pd
import joblib as jl
import numpy as np
from os.path import join
from tqdm import tqdm

In [18]:
from src.data import USED_SECTORS

YEARS = range(2007, 2016)
SECTORS = USED_SECTORS
SECTORS

['Industrials',
 'Financials',
 'Consumer Discretionary',
 'Information Technology',
 'Health Care',
 'Real Estate']

In [3]:
model.save_rules(folder=".")

In [4]:
rules_lvl1 = pd.read_csv("lvl1_R.txt", sep="\t", header=None, names=["id", "items", "class", "support", "confidence", "length"])
print(rules_lvl1["class"].value_counts())
rules_lvl2 = pd.read_csv("lvl2_R.txt", sep="\t", header=None, names=["id", "items", "class", "support", "confidence", "length"])
print(rules_lvl2["class"].value_counts())

1    1597
2     223
0     200
Name: class, dtype: int64
1    366282
2      2154
0      1999
Name: class, dtype: int64


In [5]:
df = pd.read_csv("../data/processed/SP500_technical_discretized/DENSE/AAPL.csv")
df.head()

Date SMA5-20 SMA8-15 SMA20-50 EMA5-20 EMA8-15 EMA20-50 MACD12-26  \
0  2007-01-03     NaN     NaN      NaN     NaN     NaN      NaN       NaN   
1  2007-01-04     NaN     NaN      NaN     NaN     NaN      NaN       NaN   
2  2007-01-05     NaN     NaN      NaN     NaN     NaN      NaN       NaN   
3  2007-01-08     NaN     NaN      NaN     NaN     NaN      NaN       NaN   
4  2007-01-09     NaN     NaN      NaN     NaN     NaN      NaN       NaN   

  AO14 ADX14  ... PVO14       ADL        OBV FI13 FI50       Open       High  \
0  NaN   NaN  ...   NaN  (-1e9:0]    (0:1e9]  NaN  NaN  12.327143  12.368571   
1  NaN   NaN  ...   NaN   (0:1e9]    (0:1e9]  NaN  NaN  12.007143  12.278571   
2  NaN   NaN  ...   NaN   (0:1e9]    (0:1e9]  NaN  NaN  12.252857  12.314285   
3  NaN   NaN  ...   NaN  (-1e9:0]    (0:1e9]  NaN  NaN  12.280000  12.361428   
4  NaN   NaN  ...   NaN   (0:1e9]  (1e9:inf)  NaN  NaN  12.350000  13.282857   

         Low      Close     Volume  
0  11.700000  11.971429  309579900  
1  11.974286  12.237143  211815100  
2  12.057143  12.150000  208685400  
3  12.182858  12.210000  199276700  
4  12.164286  13.224286  837324600  

[5 rows x 28 columns]

In [6]:
df.columns

Index(['Date', 'SMA5-20', 'SMA8-15', 'SMA20-50', 'EMA5-20', 'EMA8-15',
       'EMA20-50', 'MACD12-26', 'AO14', 'ADX14', 'WD14', 'PPO12_26', 'RSI14',
       'MFI14', 'TSI', 'SO14', 'CMO14', 'ATRP14', 'PVO14', 'ADL', 'OBV',
       'FI13', 'FI50', 'Open', 'High', 'Low', 'Close', 'Volume'],
      dtype='object')

In [ ]:
model.lvl1_rules_[0].item_ids

{5, 24, 34, 42, 44, 57}

In [9]:
model._class_dict[model.lvl1_rules_[0].class_id]

'1'

In [24]:
from src.data.ta import UP, DOWN, TA_DISAGREEMENT


def compute_rule_disagreement(model, rule, disagreement_dict):
    label = int(model._class_dict[rule.class_id])

    if label == 1:
        return 0

    for item_id in rule.item_ids:
        column_id, interval = model._item_id_to_item[item_id]
        column_name = model._column_id_to_name[column_id]

        try:
            dis = disagreement_dict[column_name][label].get(interval, 0)
            if dis > 0:
                print(column_name, interval, label)
            return dis
        except:
            print(column_name, column_id, interval)
            return 0


def compute_disagreements(model, disagreement_dict): 
    lvl1_disag = list(
        map(
            lambda r: compute_rule_disagreement(model, r, disagreement_dict), model.lvl1_rules_
        )
    )

    lvl2_disag = list(
        map(
            lambda r: compute_rule_disagreement(model, r, disagreement_dict), model.lvl2_rules_
        )
    )

    return lvl1_disag, lvl2_disag

In [ ]:
stats = list()
models_by_year = dict()

for year in tqdm(YEARS):
    
    model_by_sector = dict()
    
    for sector in tqdm(SECTORS, leave=False):

        print("Loading model...")
        path = f"../output/sectors/out_{year}_L3/models/best_model_{sector}.joblib"
        model = jl.load(path)["clf"]
        model_by_sector[sector] = model
    
        print("Computing disagreements...")
        lvl1_dis, lvl2_dis = compute_disagreements(model, TA_DISAGREEMENT)
        
        filtered_1 = [i for i, count in enumerate(lvl1_dis) if count > 0]
        filtered_2 = [i for i, count in enumerate(lvl2_dis) if count > 0]
        
        stats.append(
            dict(
                year=year,
                sector=sector,
                total_l1=len(lvl1_dis),
                filtered_l1=len(filtered_1),
                total_l2=len(lvl2_dis),
                filtered_l2=len(filtered_2)
            )
        )
        
    models_by_year[year] = model_by_sector

  0%|          | 0/6 [00:00<?, ?it/s]

Loading model...


Computing disagreements...
TSI 13 (-inf:-25]
TSI 13 (-25:0]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
PPO12_26 (0:5] 0
TSI 13 (-inf:-25]
AO14 (0:50] 0
AO14 (-50:0] 2
AO14 (-50:0] 2
AO14 (-50:0] 2
AO14 (-50:0] 2
SMA20-50 (5:inf) 2
TSI 13 (-inf:-25]
AO14 (-50:0] 2
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-25:0]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
SMA20-50 (5:inf) 2
SMA20-50 (5:inf) 2
SMA20-50 (5:inf) 2
SMA20-50 (5:inf) 2
SMA20-50 (5:inf) 2
SMA20-50 (5:inf) 2
AO14 (-50:0] 2
SMA20-50 (5:inf) 2
TSI 13 (-inf:-25]
TSI 13 (-25:0]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
AO14 (0:50] 0
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
TSI 13 (-inf:-25]
PPO12_26 (0:5] 0
TSI 13 (-inf:-25]
AO14 (0:50] 0


 17%|█▋        | 1/6 [00:27<02:17, 27.47s/it]

Loading model...
Computing disagreements...
PPO12_26 (-5:0] 2
AO14 (-50:0] 2
PPO12_26 (-5:0] 2
AO14 (-50:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
AO14 (-50:0] 2
AO14 (-50:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
AO14 (-50:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
PPO12_26 (-5:0] 2
AO14 (-50:0] 2


...

Computing disagreements...
SMA5-20 (5:inf) 2
AO14 (50:100] 0
AO14 (50:100] 0
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
AO14 (50:100] 0
AO14 (50:100] 0
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
TSI 13 (-25:0]
AO14 (50:100] 0
SMA5-20 (5:inf) 2
MACD12-26 (5:inf) 2
SMA5-20 (5:inf) 2
AO14 (50:100] 0
SMA5-20 (5:inf) 2
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
SMA5-20 (5:inf) 2
Loading model...
Computing disagreements...
EMA5-20 (5:inf) 2
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
SMA8-15 (5:inf) 2
EMA5-20 (5:inf) 2
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (-50:0] 2
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
AO14 (50:100] 0
A


 50%|█████     | 3/6 [04:13<04:08, 82.88s/it]

Loading model...
Computing disagreements...
AO14 (50:100] 0
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA20-50 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
AO14 (50:100] 0
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
AO14 (50:100] 0
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
EMA20-50 (5:inf) 2
SMA5-20 (5:inf) 2
AO14 (50:100] 0
SMA5-20 (5:inf) 2
AO14 (-50:0] 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
EMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:inf) 2
SMA5-20 (5:


 67%|██████▋   | 4/6 [07:18<04:06, 123.24s/it]

Loading model...


In [ ]:
df_stats = pd.DataFrame(stats)